<center><img src="https://github.com/pandas-dev/pandas/raw/main/web/pandas/static/img/pandas.svg" alt="pandas Logo" style="width: 800px;"/></center>

# Pandas 9: Multi-index DataFrames
---

### In many instances, tabular data may best be represented with more than a single row index. For the case of NYSM hourly data files, which have 126 stations each with 13 sets of 5-minute obs, we definitely want to take advantage of using Multi-index Dataframes.

## Overview
1. Open an hour's worth of NYSM data using a single row index dataframe
1. Review selection and conditional selection methodology
1. Create a dataframe with station ID and date/time as the two row indices
1. Use selection and conditions on a multi-index dataframe
1. Briefly define tuples as opposed to lists in Python
1. Work with the time index as a Datetime object

## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| Pandas notebooks 1-8 | Necessary | |

* **Time to learn**: 15 minutes

## Imports

In [ ]:
import pandas as pd
from datetime import datetime 

#### Open an hour's worth of NYSM data using a single row index dataframe</span>

In [ ]:
nysm_data_file = '/spare11/atm533/data/nysm_data_2021090202a.csv'

In [ ]:
df = pd.read_csv(nysm_data_file)
# Look at the first few rows
df.head(3)

Remind ourselves that the default `DataFrame`'s index is a special type of Python object, called a *RangeIndex*.

In [ ]:
df.index

#### Review selection and conditional selection methodology

Here we have multiple stations and multiple times. We can select rows/columns, set conditions, and make further selections based on those conditions as we did in the **03_Pandas_IndexSubsetsConditonals** notebook. 

In [ ]:
df[df['station']=='VOOR'] # Voorheesville, NY

Create a second dataframe that first contains just VOOR rows, then further subset by choosing one time.

In [ ]:
df2 = df[df['station']=='VOOR']
df2[df2['time'] == '2021-09-02 02:50:00 UTC'] # we haven't recast this as a Datetime object ... it's just a string

However, there is a better way! Since our DataFrame consists of one station after another, each associated with a number of discrete times, let's create a **multi-indexed** DataFrame, that has *station* as its outer row index and *time* as its inner.

#### Create a dataframe with station ID and date/time as the two row indices

In [ ]:
df.set_index(['station', 'time'], inplace = True)

<div class="alert alert-block alert-warning">
    <b>Note:</b> <code>inplace</code> means that the df object gets <i>re-created with its new indexes</i>. It's convenient, but if at any point we wish to re-run cells beyond this point, it is better to start from the beginning to ensure that the <code>df</code> object conforms to whatever code cell operates on it.</div>

In [ ]:
df

In [ ]:
df.index

The date/time index is currently a string. Let's do this nifty trick to convert it to a `datetime` object.

In [ ]:
df.index = df.index.set_levels([df.index.levels[0], pd.to_datetime(df.index.levels[1])])

In [ ]:
#Examine first three row indices
df.index[:3]

#### Use selection and conditions on a multi-index dataframe

Select a column in the usual way.

In [ ]:
df.loc['VOOR']

Use `loc` to select not only the station id, but also a specific time: we pass in a `tuple` to the `loc` method

#### Briefly define **tuples** as opposed to **lists** in Python

A `tuple` is a core Python class, similar to but distinct from a `list`
1. Tuples are enclosed in parentheses (); lists are enclosed in brackets []
1. Elements in a `tuple` are *immutable* (i.e. can't be changed), but `list` elements can be changed.

In [ ]:
a = (4,7,9) # a tuple
print (a)
print(a[2])
# this next line won't work; comment it out to see:
# a[2] = 8

In [ ]:
b = [4, 7, 9]
print (b)
print (b[2])
# this will work:
b[2] = 8
print(b)

<div class="alert alert-block alert-info">
    <b>Tip:</b> Some Pandas methods accept <b>tuples</b> as their arguments, although <b>lists</b> will usually work too. When in doubt, append a <b>?</b> to the method call to see the documentation.</div>

What can be confusing is that just because something is enclosed in brackets, that doesn't mean it's a Python list object. In terms of Pandas, the DataFrame's `loc` method typically expects a string that's enclosed in brackets.

<div class="alert alert-block alert-info">
    <b>Tip:</b> Note: we can pass in the requested time as a <b>string</b> ... it will work!</div>

In [ ]:
df.loc[('VOOR','2021-09-02 02:45:00 UTC')]

As above, but also select a particular column:

In [ ]:
df.loc[('VOOR','2021-09-02 02:45:00 UTC'),'temp_2m [degC]' ]

Taking advantage of *multi-indexing* allows us to write selection criteria that is more intuitive than how we've previously defined and utilized conditonal statements in our selection criteria (as in our cell earlier in the notebook with nested data frame object names). It also executes quicker!

Pass in multiple columns (either as a list or a tuple) ... get back a `DataFrame` whose columns are the ones we selected

In [ ]:
df.loc[('VOOR','2021-09-02 02:45:00 UTC'),('temp_2m [degC]','precip_incremental [mm]')]

Pass in multiple indexes and multiple columns also returns `DataFrame`s:
1. Two outer and one inner index:

In [ ]:
df.loc[(('VOOR','KIND'),'2021-09-02 02:45:00 UTC'),('temp_2m [degC]','precip_incremental [mm]')]

2. Two outer and two inner:

In [ ]:
df.loc[(('VOOR','KIND'),('2021-09-02 02:45:00 UTC','2021-09-02 02:55:00 UTC')),('temp_2m [degC]','precip_incremental [mm]')]

3. One outer and two inner:

In [ ]:
df.loc[('VOOR',('2021-09-02 02:45:00 UTC','2021-09-02 02:55:00 UTC')),('temp_2m [degC]','precip_incremental [mm]')]

A more efficient way to get all stations at a particular time is via Pandas' `xs` DataFrame method.

In [ ]:
# Pass in one index value and what index it belongs to
df.xs('2021-09-02 02:45:00 UTC', level='time')

Include just a *list* of columns (a *tuple* won't work here)

In [ ]:
df.xs('2021-09-02 02:45:00 UTC', level = 'time')[['temp_2m [degC]','temp_9m [degC]']]

#### Work with the time index as a Datetime object:

Pandas' handling of `datetime` objects is incredibly powerful (see https://pandas.pydata.org/pandas-docs/stable/user_guide/timeseries.html) . Below, we select 3 times using the `date_range` method.

In [ ]:
timeRange = pd.date_range('2021-09-02 02:25', periods=3, freq='5min')

In [ ]:
df.loc[('MANH',timeRange.values),('max_wind_speed_prop [m/s]', 'max_wind_speed_sonic [m/s]')]

---
## Summary
* One can recast a Pandas `DataFrame` so it leverages multi-indexing
* Selecting and specifying conditions on a multi-index `DataFrame` work just as in a single-index `DataFrame`
* Pandas has a large set of utilities to work with time-series based data. `xs` is one such method.
* In Python, **tuples** are akin to **lists**, but a tuple's elements are *immutable*.

### What's Next?
In the next notebook, we will merge DataFrames that have different row indexes.
## Resources and References
1. [MetPy Monday Episode 96](https://www.youtube.com/watch?v=yQ5IxnZouKo&list=PLQut5OXpV-0ir4IdllSt1iEZKTwFBa7kO&index=87&ab_channel=Unidata)
1. https://www.geeksforgeeks.org/python-difference-between-list-and-tuple/
1. https://stackoverflow.com/questions/8900166/whats-the-difference-between-lists-enclosed-by-square-brackets-and-parentheses
1. [Time series in Pandas](https://pandas.pydata.org/pandas-docs/stable/user_guide/timeseries.html)